In [1]:
#Functions for Corpora and Topic models
import gensim
import gensim.corpora as corpora
import os
import pyLDAvis.gensim
import pickle 
import pyLDAvis
seed = 61

In [2]:
#FIRST LOOK IN MODEL STILL CONTAINING VERBS
#load model (remark: has been saved during model selection)
num_topics = 100
model_train = gensim.models.LdaModel.load('./results/lda_'+str(num_topics)+'.model')

#load ldavis: Analyse 
pyLDAvis.enable_notebook()
LDAvis_data_filepath = os.path.join('./results/ldavis_prepared_'+str(num_topics))
with open(LDAvis_data_filepath, 'rb') as f:
    ldavis = pickle.load(f)
ldavis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
13     0.058103  0.004891       1        1  3.677448
88     0.081004 -0.010450       2        1  2.803120
6      0.002168 -0.011248       3        1  2.269924
18    -0.031608 -0.027199       4        1  2.174124
89     0.035186 -0.011124       5        1  2.023261
...         ...       ...     ...      ...       ...
91    -0.029239  0.096308      96        1  0.414854
31     0.002213 -0.041863      97        1  0.414232
81     0.090494  0.123454      98        1  0.395196
49     0.056350  0.082565      99        1  0.386949
47    -0.010329  0.115358     100        1  0.241427

[100 rows x 5 columns], topic_info=         Term         Freq        Total  Category  logprob  loglift
47       baby  2387.000000  2387.000000   Default  30.0000  30.0000
71       time  2006.000000  2006.000000   Default  29.0000  29.0000
283        go  1888.000000  1888.000000   Default  28.0000  28.0000
1236    na_na   199.000000   199.000000   Default  27.0000  27.0000
462       say  1789.000000  1789.000000   Default  26.0000  26.0000
...       ...          ...          ...       ...      ...      ...
23    getting     4.006039   284.578571  Topic100  -5.0077   1.7632
337      said     4.543287   967.759173  Topic100  -4.8818   0.6650
369      well     4.494479   871.534162  Topic100  -4.8926   0.7590
47       baby     4.434312  2387.754386  Topic100  -4.9061  -0.2624
192     might     4.006293   699.685603  Topic100  -5.0076   0.8636

[6444 rows x 6 columns], token_table=      Topic      Freq  Term
term                       
1334      1  0.049350  able
1334      2  0.049350  able
1334      3  0.024675  able
1334      4  0.024675  able
1334      5  0.024675  able
...     ...       ...   ...
2419     50  0.044140  zero
2419     53  0.044140  zero
2419     67  0.044140  zero
2419     69  0.088280  zero
2419     77  0.044140  zero

[68377 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[14, 89, 7, 19, 90, 60, 65, 28, 52, 4, 81, 11, 15, 58, 77, 79, 18, 20, 72, 22, 91, 5, 51, 8, 36, 39, 66, 78, 74, 67, 63, 93, 56, 68, 37, 64, 55, 47, 6, 3, 26, 83, 53, 99, 12, 76, 9, 96, 59, 62, 49, 46, 35, 94, 100, 61, 17, 43, 30, 69, 98, 80, 71, 97, 87, 86, 75, 2, 27, 24, 44, 42, 57, 41, 70, 85, 54, 31, 21, 95, 88, 1, 40, 33, 84, 45, 29, 25, 13, 38, 23, 16, 10, 34, 73, 92, 32, 82, 50, 48])

Results (took lambda = 0.8 for analysis) of first look at data:
- top left: someone has left, should come back: 68 (gone, come back), 92 (come_back, hear, stuff), 100 (middle, alone bed)
    - only less relevant topics
- bottom left quadrant: needing girl, never let go (7,4,8).
    - second most relevant cluster
- bottom right seems more hip hop dominated from the use of language (1,2,3).
    - biggest clusters here
- little amounts of outliers at the top and bottom which are also less relevant

In [3]:
#Wanna look at topics per genre: Need to create corporas per genre and the original df
from gensim.utils import simple_preprocess
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
import pandas as pd

stop_words = stopwords.words('english')
stop_words.extend(['from', 'la','oh','also', 'yeah', 'ooh','uh','chorus','verse','outro','bridge'])
                  
def sent_to_words(sentences):
    for sentence in sentences:
        # deacc=True removes punctuations
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))
def remove_stopwords(texts, stop_words):
    return [[word for word in simple_preprocess(str(doc)) 
             if word not in stop_words] for doc in texts]
def bigrams(words, bi_min=10):
    bigram = gensim.models.Phrases(words, min_count = bi_min)
    bigram_mod = gensim.models.phrases.Phraser(bigram)
    return bigram_mod

def lyric_to_corpora(lyric_series, stop_words, id2word=None):
    data = lyric_series.values.tolist()
    data_words = list(sent_to_words(data))
    data_words = remove_stopwords(data_words, stop_words)
    #make bigrams
    bigram_mod = bigrams(data_words)
    data_bigrams = [bigram_mod[lyric] for lyric in data_words]
    if id2word is None:
        #Create Dictionary and filter extremes
        id2word = corpora.Dictionary(data_bigrams)
        id2word.filter_extremes(no_below=10, no_above=0.35)
    #Create Corpus
    corpus = [id2word.doc2bow(text) for text in data_bigrams]
    return corpus, id2word
df_train = pd.read_csv(os.path.join("results", "df_train"), encoding='utf-8')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\benja\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [4]:
#TO BETTER IDENTIFY GENRES PER TOPIC: ALSO LOOK AT TOPICS PER GENRE
from pprint import pprint
num_topics = 100
genres = list(set(df_train.genre.values))
for genre in genres:
    #Get genre-data
    print("GENRE: "+str(genre))
    df_genre = df_train[df_train["genre"]==genre]
    corpus_genre, id2word_genre = lyric_to_corpora(df_genre.lyric_processed, stop_words)
    lda_model = gensim.models.LdaMulticore(corpus=corpus_genre,
                                       id2word=id2word_genre,
                                       num_topics=num_topics,
                                           iterations=1000,
                                      alpha=0.125,
                                          random_state=seed)
    pprint(lda_model.print_topics())
    print("-----------------------------------------------------")

GENRE: country
[(91,
  '0.046*"get" + 0.043*"son" + 0.043*"say" + 0.034*"please" + 0.030*"near" + '
  '0.030*"go" + 0.026*"til" + 0.021*"take" + 0.018*"well" + 0.017*"away"'),
 (3,
  '0.044*"need" + 0.044*"mama" + 0.031*"man" + 0.031*"want" + 0.031*"takes" + '
  '0.031*"party" + 0.026*"cause" + 0.026*"baby" + 0.026*"say" + 0.026*"eyes"'),
 (94,
  '0.065*"meet" + 0.057*"look" + 0.046*"running" + 0.039*"late" + '
  '0.033*"better" + 0.033*"see" + 0.029*"fool" + 0.024*"wait" + 0.021*"still" '
  '+ 0.021*"minute"'),
 (12,
  '0.135*"broke" + 0.073*"well" + 0.042*"back" + 0.042*"til" + 0.042*"pretty" '
  '+ 0.042*"top" + 0.031*"got" + 0.031*"man" + 0.031*"see" + 0.031*"said"'),
 (38,
  '0.061*"time" + 0.035*"lord" + 0.032*"could" + 0.029*"take" + 0.026*"never" '
  '+ 0.022*"old" + 0.022*"christmas" + 0.019*"break" + 0.019*"give" + '
  '0.019*"hand"'),
 (93,
  '0.066*"get" + 0.027*"way" + 0.027*"lord" + 0.027*"feeling" + 0.027*"new" + '
  '0.027*"good" + 0.020*"well" + 0.020*"man" + 0.020*"he

Results:
- pop:
    - much on love in presence
        - woman, heart, love
        - come, mine, night
        - heart, right, tonight
        - love, get, baby
    - some on being alone:
        - take, ever, forever, waiting
        - believe, still time, man, let, let_go
        - alone, say, felt, still
        - night, could, dark, ... ,lonely
     - some around sun
        - high, sun, round, dance
        - child, star, lay, sun
- r-b:
    - love from a sad perspective:
        - girl, come_back, wanna
        - wanna, tell, hold, tonight, ..., girl, wait
        - heart, king, never, ..., come_back, girls
        - tell, never, loved
        - feel, feels_like, girl, tears
        - ... really most of it
    - general mostly sad topics
 -	Rock
    - Search of better life:
        - Keep, go, walk, away, house
        - Learn, better, home, never, bad
        - Gonna, say, think, got, let, turn
    - Never leaving love:
        - Never, baby, got, leave, babe
        - Burn, name, never
        - Eyes, tell, ever, keep, always
    - Sky, waves, :more metaphors
        - Sky, got, time, bad, rain, die
        - Waves, sky, goodbye, love, wide
    - Feeling shitty:
        - Away, see, fuck, pain
        - Still, lost, love
        - Tired, time, sleep, way
        - Need, broken, one
    - Turn in general big concept
-	Country:
    - Talk about lord:
        - Time, lord, could, take
        - Get, way, lord, feeling, new
    - Referening old love:
        - Let, old, time, wanna, still, us, live
        - Took, wanna, never, heart, feel
        - pet names like darling or honey
        - Still, would, way, half, broke, heart
    - Some stuff about life:
        - home, son
        - Meet, look, running, late, better, see
        - Every, man, ever, wanna, let, lives
        - Still, mine, time, world, day
        - Never, say, change, little, people
        - Nobody, got, good, day, long, time
    - Obvious words:
        - country, California, river, mountain
    - Kinda seems like more processed pain in comparison to other genres
-	Rap:
    - Different vocabulary: bitch, ya, yo, motherfucker,
    - “Love”
        - Love, still, day, together
        - Us, world, new, face, name
        - Love, girl, bitch, would, girls
        - Roll, ride, way, mind, touch, baby, cold, love
        - Bitch, done, would, maybe, yo, damn, hate, ass
    - Being real:
        - Team, bitch, love, ya, feel, real
        - Real, still, ya, yo, long, hold
        - Good, feel, yo, could, real
    - Lord, jesus
        - Jesus, damn, tryna, us, gon, lord
        - God, put, everybody, nobody
    - Obvious words:
        - nigga, bitch, motherfucker, mc, rap, high

 
  

In [5]:
#FOR TOTAL MODEL (NOT PER GENRE), LOOK AT TOP 20 MOST RELEVANT TOPICS
pprint(model_train.print_topics(30,10))

[(34,
  '0.021*"come" + 0.018*"go" + 0.017*"us" + 0.016*"let" + 0.013*"home" + '
  '0.012*"around" + 0.010*"man" + 0.010*"world" + 0.009*"life" + 0.009*"tell"'),
 (51,
  '0.020*"ah_ah" + 0.013*"want" + 0.013*"would" + 0.012*"keep" + 0.009*"long" '
  '+ 0.008*"never" + 0.008*"told" + 0.008*"around" + 0.008*"cause" + '
  '0.008*"getting"'),
 (90,
  '0.010*"make" + 0.010*"back" + 0.009*"feel" + 0.009*"cause" + 0.008*"go" + '
  '0.008*"gotta" + 0.008*"brand_new" + 0.008*"never" + 0.007*"time" + '
  '0.007*"man"'),
 (80,
  '0.015*"think" + 0.012*"let" + 0.010*"something" + 0.010*"baby" + '
  '0.010*"tonight" + 0.009*"right" + 0.009*"tell" + 0.008*"best" + '
  '0.008*"gonna" + 0.007*"come"'),
 (1,
  '0.021*"say" + 0.019*"gone" + 0.017*"baby" + 0.017*"tell" + 0.014*"ya" + '
  '0.014*"back" + 0.013*"cause" + 0.012*"come_back" + 0.011*"gonna" + '
  '0.010*"believe"'),
 (12,
  '0.016*"right" + 0.014*"time" + 0.014*"girl" + 0.013*"care" + 0.012*"go" + '
  '0.012*"nothing" + 0.012*"tired" + 0.011*

Results:
- Hard time seperating and lots similiar topics
- distinction of rap due to vocabulary still very easy: ya, bitch, nigga, niggas: rap
- 3: way, never, home, wanna, man: seems like country: woman at home, man on some journey
- A lot is really hard to distinguish by us (what about a machine learning classifier?)

In [6]:
#NOW MODEL WITHOUT VERBS: GET MODEL AND VISUALIZE
def save_model_and_ldavis(corpus,id2word,num_topics,alpha,seed,name=""):
    lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                               id2word=id2word,
                                               num_topics=num_topics,
                                               alpha=alpha,
                                               eta=1.0/num_topics,
                                            iterations=1000,
                                           random_state=seed)
    if not name:
        name = str(num_topics)
    lda_model.save('./results/lda_'+name+'.model')
    # Visualize the topics
    pyLDAvis.enable_notebook()
    LDAvis_data_filepath = os.path.join('./results/ldavis_prepared_'+name)
    # # this is a bit time consuming - make the if statement True
    # # if you want to execute visualization prep yourself
    if not os.path.exists(LDAvis_data_filepath):
        LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
        with open(LDAvis_data_filepath, 'wb') as f:
            pickle.dump(LDAvis_prepared, f)
    else: 
        # load the pre-prepared pyLDAvis data from disk
        with open(LDAvis_data_filepath, 'rb') as f:
            LDAvis_prepared = pickle.load(f)
    pyLDAvis.save_html(LDAvis_prepared, './results/ldavis_prepared_'+ str(num_topics) +'.html')
    return LDAvis_prepared

corpus_train_extended = corpora.MmCorpus(os.path.join("results", "corpus_train_extended"))
corpus_test_extended = corpora.MmCorpus(os.path.join("results", "corpus_test_extended"))
id2word_train_extended = corpora.Dictionary.load(os.path.join("results", "id2word_train_extended"))
#USE PARAMETERS OF MODEL STILL USING VERBS: OTHERWISE TOO MUCH EFFORT
num_topics=100
alpha=0.125
name = str(num_topics)+"_extended"
#FIT, SAVE AND VISUALIZE MODEL
LDAvis = save_model_and_ldavis(corpus_train_extended,id2word_train_extended,num_topics,alpha=alpha,seed=seed,name=name)
LDAvis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
87    -0.014127  0.010605       1        1  3.114917
43    -0.080102 -0.039025       2        1  2.077151
69     0.007719  0.027304       3        1  2.026817
92    -0.040386 -0.009106       4        1  1.957395
95    -0.054732 -0.026261       5        1  1.944352
...         ...       ...     ...      ...       ...
4      0.033667  0.096833      96        1  0.385906
15     0.174425 -0.047136      97        1  0.377500
46     0.033902  0.071209      98        1  0.305951
89    -0.057169 -0.181094      99        1  0.261150
59    -0.043954 -0.175479     100        1  0.250274

[100 rows x 5 columns], topic_info=      Term         Freq        Total  Category  logprob  loglift
44    baby  2379.000000  2379.000000   Default  30.0000  30.0000
101  never  2161.000000  2161.000000   Default  29.0000  29.0000
56    home   837.000000   837.000000   Default  28.0000  28.0000
130    way  1602.000000  1602.000000   Default  27.0000  27.0000
164   girl  1357.000000  1357.000000   Default  26.0000  26.0000
..     ...          ...          ...       ...      ...      ...
631    big     3.413948   380.038422  Topic100  -5.0936   1.2780
101  never     3.420581  2161.185197  Topic100  -5.0916  -0.4582
45    back     3.417902  1836.228717  Topic100  -5.0924  -0.2961
4     away     3.416153   817.336967  Topic100  -5.0929   0.5128
83    fall     3.414414   394.421397  Topic100  -5.0934   1.2410

[6340 rows x 6 columns], token_table=      Topic      Freq  Term
term                       
1308      1  0.023900  able
1308      3  0.023900  able
1308      4  0.023900  able
1308      5  0.023900  able
1308     10  0.023900  able
...     ...       ...   ...
917      69  0.072553  zone
917      70  0.024184  zone
917      83  0.024184  zone
917      85  0.024184  zone
917      86  0.024184  zone

[67039 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[88, 44, 70, 93, 96, 15, 83, 8, 80, 89, 52, 94, 22, 82, 23, 49, 86, 36, 3, 78, 38, 30, 51, 95, 73, 24, 28, 48, 75, 77, 99, 7, 34, 76, 41, 40, 84, 31, 61, 13, 74, 39, 45, 37, 69, 46, 18, 2, 62, 6, 91, 4, 66, 85, 50, 87, 67, 79, 65, 33, 71, 98, 55, 68, 97, 20, 100, 19, 21, 54, 92, 17, 59, 35, 25, 11, 57, 27, 29, 14, 63, 43, 56, 12, 53, 1, 10, 42, 58, 64, 81, 26, 32, 9, 72, 5, 16, 47, 90, 60])

RESULTS: 
- very different distribution, a lot less spread and outliers seem to concentrate towards the right center
- most topics seem to be similiar
- Rap and country topics seem to still be distinguishable from others
- does the classifier perform better or worse now? lacking information vs less too general words

In [7]:
#FOR TOTAL MODEL (NOT PER GENRE), LOOK AT TOP 20 MOST RELEVANT TOPICS
model_train_extended = gensim.models.LdaModel.load('./results/lda_'+name+'.model')
#Look at top 20 significant topics in general
pprint(model_train_extended.print_topics(30,10))

[(69,
  '0.013*"night" + 0.012*"rolling" + 0.011*"world" + 0.010*"tonight" + '
  '0.010*"storm" + 0.010*"people" + 0.010*"black" + 0.009*"city" + '
  '0.008*"still" + 0.008*"girl"'),
 (23,
  '0.050*"never" + 0.010*"away" + 0.009*"home" + 0.009*"going" + 0.009*"girl" '
  '+ 0.008*"cause" + 0.008*"baby" + 0.008*"time" + 0.007*"still" + '
  '0.007*"ever"'),
 (9,
  '0.020*"stop" + 0.015*"heart" + 0.015*"nothing" + 0.014*"late" + 0.013*"old" '
  '+ 0.012*"mistakes" + 0.012*"tried" + 0.012*"thinking" + 0.011*"still" + '
  '0.011*"low"'),
 (34,
  '0.024*"sorry" + 0.017*"girl" + 0.014*"baby" + 0.014*"away" + 0.010*"er" + '
  '0.010*"back" + 0.009*"enough" + 0.009*"fell" + 0.008*"going" + '
  '0.008*"shit"'),
 (2,
  '0.019*"way" + 0.015*"baby" + 0.012*"cause" + 0.012*"lost" + 0.011*"right" + '
  '0.010*"girl" + 0.010*"better" + 0.009*"much" + 0.009*"found" + 0.008*"fly"'),
 (5,
  '0.021*"way" + 0.015*"hear" + 0.013*"cause" + 0.013*"place" + 0.013*"never" '
  '+ 0.010*"try" + 0.009*"thanks" + 0.

Results:
- more words that seem to give more information about the content
- words like love missing that would usually give important information

Remark: Did not look at topics per genre here, because understanding of genres already exists. 